In [0]:
!pip install xcodec2==0.1.3
!pip install vllm -U
!pip install torch==2.5.1 torchaudio==2.5.1 torchvision==0.20.1


In [0]:
%restart_python

In [0]:
from transformers import pipeline, AutoTokenizer
import torch
import soundfile as sf
from xcodec2.modeling_xcodec2 import XCodec2Model
from IPython import display
import torchaudio
from vllm import LLM, SamplingParams
import numpy as np
import re

llm = LLM(model="srinivasbilla/llasa-3b", gpu_memory_utilization=0.5, max_model_len=4096, enable_prefix_caching=True)
tokenizer = AutoTokenizer.from_pretrained('srinivasbilla/llasa-3b')

model_path = "srinivasbilla/xcodec2"
 
Codec_model = XCodec2Model.from_pretrained(model_path)
Codec_model.eval().cuda()

whisper_turbo_pipe = pipeline("automatic-speech-recognition", model="openai/whisper-large-v3-turbo", device='cuda')

2025-01-21 19:26:54.419785: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


INFO 01-21 19:27:02 config.py:2272] Downcasting torch.float32 to torch.float16.
INFO 01-21 19:27:14 config.py:510] This model supports multiple tasks: {'reward', 'classify', 'generate', 'score', 'embed'}. Defaulting to 'generate'.
INFO 01-21 19:27:14 llm_engine.py:234] Initializing an LLM engine (v0.6.6.post1) with config: model='srinivasbilla/llasa-3b', speculative_config=None, tokenizer='srinivasbilla/llasa-3b', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, override_neuron_config=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.float16, max_seq_len=4096, download_dir=None, load_format=LoadFormat.AUTO, tensor_parallel_size=1, pipeline_parallel_size=1, disable_custom_all_reduce=False, quantization=None, enforce_eager=False, kv_cache_dtype=auto, quantization_param_path=None, device_config=cuda, decoding_config=DecodingConfig(guided_decoding_backend='xgrammar'), observability_config=ObservabilityConfig(otlp_traces_endpoint=None, collect_model_forward_t

Loading safetensors checkpoint shards:   0% Completed | 0/3 [00:00<?, ?it/s]


INFO 01-21 19:27:51 model_runner.py:1099] Loading model weights took 6.3910 GB
INFO 01-21 19:27:52 worker.py:241] Memory profiling takes 1.05 seconds
INFO 01-21 19:27:52 worker.py:241] the current vLLM instance can use total_gpu_memory (44.53GiB) x gpu_memory_utilization (0.50) = 22.26GiB
INFO 01-21 19:27:52 worker.py:241] model weights take 6.39GiB; non_torch_memory takes 0.11GiB; PyTorch activation peak memory takes 1.79GiB; the rest of the memory reserved for KV Cache is 13.98GiB.
INFO 01-21 19:27:53 gpu_executor.py:76] # GPU blocks: 8178, # CPU blocks: 2340
INFO 01-21 19:27:53 gpu_executor.py:80] Maximum concurrency for 4096 tokens per request: 31.95x
INFO 01-21 19:27:58 model_runner.py:1415] Capturing cudagraphs for decoding. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI. If out-of-memory error occurs during cudagraph capture, consider decreasing `gpu_memory_utilizat

Capturing CUDA graph shapes: 100%|██████████| 35/35 [00:31<00:00,  1.11it/s]

INFO 01-21 19:28:29 model_runner.py:1535] Graph capturing finished in 32 secs, took 0.77 GiB
INFO 01-21 19:28:29 llm_engine.py:431] init engine (profile, create kv cache, warmup model) took 37.82 seconds


In [0]:

def ids_to_speech_tokens(speech_ids):
 
    speech_tokens_str = []
    for speech_id in speech_ids:
        speech_tokens_str.append(f"<|s_{speech_id}|>")
    return speech_tokens_str

def extract_speech_ids(speech_tokens_str):
    return [int(x.replace('s_', '')) for x in speech_tokens_str[2:-2].split('|><|')]


def text_to_speech(sample_audio_path, target_text, sampling_params, prompt_text=None):
    waveform, sample_rate = torchaudio.load(sample_audio_path)

    # Check if the audio is stereo (i.e., has more than one channel)
    if waveform.size(0) > 1:
        # Convert stereo to mono by averaging the channels
        waveform_mono = torch.mean(waveform, dim=0, keepdim=True)
    else:
        # If already mono, just use the original waveform
        waveform_mono = waveform

    waveform_16k = torchaudio.transforms.Resample(orig_freq=sample_rate, new_freq=16000)(waveform_mono)
    torchaudio.save('/local_disk0/input.wav', waveform_16k, 16000)

    # only 16khz speech support!
    prompt_wav, sr = sf.read("/local_disk0/input.wav") # English prompt
    prompt_wav = torch.from_numpy(prompt_wav).float().unsqueeze(0)

    if prompt_text is None:
        prompt_text = whisper_turbo_pipe('/local_disk0/input.wav')['text'].strip()
        print(prompt_text)

    input_text = prompt_text + ' ' + target_text

    #TTS start!
    with torch.no_grad():
        # Encode the prompt wav
        vq_code_prompt = Codec_model.encode_code(input_waveform=prompt_wav)

        vq_code_prompt = vq_code_prompt[0,0,:]
        # Convert int 12345 to token <|s_12345|>
        speech_ids_prefix = ids_to_speech_tokens(vq_code_prompt)

        formatted_text = f"<|TEXT_UNDERSTANDING_START|>{input_text}<|TEXT_UNDERSTANDING_END|>"

        # Tokenize the text and the speech prefix
        chat = [
            {"role": "user", "content": "Convert the text to speech:" + formatted_text},
            {"role": "assistant", "content": "<|SPEECH_GENERATION_START|>" + ''.join(speech_ids_prefix)}
        ]

        input_ids = tokenizer.apply_chat_template(
            chat, 
            tokenize=False, 
            continue_final_message=True
        )

        outputs = llm.generate([input_ids], sampling_params)

        generated_text = outputs[0].outputs[0].text
        print(generated_text)

        speech_tokens = extract_speech_ids(generated_text)
        speech_tokens = torch.tensor(speech_tokens).cuda().unsqueeze(0).unsqueeze(0)
        gen_wav = Codec_model.decode_code(speech_tokens)
    
    return gen_wav[0, 0, :].cpu().numpy(), generated_text


import re

def chunk_text(text, min_length=200):
    # Split the text into sentences using regular expression to detect sentence boundaries
    sentences = re.split(r'(?<=\.|\!|\,|\?)\s+', text)

    # Initialize variables
    chunks = []
    current_chunk = ""

    # Iterate through sentences and create chunks
    for sentence in sentences:
        # If adding this sentence exceeds the min_length, start a new chunk
        if len(current_chunk) + len(sentence) + 1 >= min_length:
            if current_chunk:
                chunks.append(current_chunk)
            current_chunk = sentence
        else:
            # Otherwise, add sentence to current chunk
            if current_chunk:
                current_chunk += " " + sentence
            else:
                current_chunk = sentence
    
    # Don't forget to append the last chunk if any
    if current_chunk:
        chunks.append(current_chunk)

    return chunks

def long_text_to_speech(sample_audio_path, target_text, prompt_text=None, chunk_length=200):
    waveform, sample_rate = torchaudio.load(sample_audio_path)

    # Check if the audio is stereo (i.e., has more than one channel)
    if waveform.size(0) > 1:
        # Convert stereo to mono by averaging the channels
        waveform_mono = torch.mean(waveform, dim=0, keepdim=True)
    else:
        # If already mono, just use the original waveform
        waveform_mono = waveform

    waveform_16k = torchaudio.transforms.Resample(orig_freq=sample_rate, new_freq=16000)(waveform_mono)
    torchaudio.save('/local_disk0/input.wav', waveform_16k, 16000)

    # only 16khz speech support!
    prompt_wav, sr = sf.read("/local_disk0/input.wav") # English prompt
    prompt_wav = torch.from_numpy(prompt_wav).float().unsqueeze(0)

    if prompt_text is None:
        prompt_text = whisper_turbo_pipe('/local_disk0/input.wav')['text'].strip()
        print(prompt_text)

    chunks = chunk_text(target_text, min_length=chunk_length)
    input_texts = [prompt_text + ' ' + chunk for chunk in chunks]

    with torch.no_grad():
        # Encode the prompt wav
        vq_code_prompt = Codec_model.encode_code(input_waveform=prompt_wav)

        vq_code_prompt = vq_code_prompt[0,0,:]
        # Convert int 12345 to token <|s_12345|>
        speech_ids_prefix = ids_to_speech_tokens(vq_code_prompt)

        formatted_texts = [f"<|TEXT_UNDERSTANDING_START|>{input_text}<|TEXT_UNDERSTANDING_END|>" for input_text in input_texts]

        # Tokenize the text and the speech prefix
        chats = [[
            {"role": "user", "content": "Convert the text to speech:" + formatted_text},
            {"role": "assistant", "content": "<|SPEECH_GENERATION_START|>" + ''.join(speech_ids_prefix)}
        ] for formatted_text in formatted_texts]

        input_ids = tokenizer.apply_chat_template(
            chats, 
            tokenize=False, 
            continue_final_message=True
        )

        outputs = llm.generate(input_ids, sampling_params)

        generated_texts = [x.outputs[0].text for x in outputs]

        speech_tokens_list = [extract_speech_ids(generated_text) for generated_text in generated_texts]
        speech_tokens = [torch.tensor(speech_tokens).cuda().unsqueeze(0).unsqueeze(0) for speech_tokens in speech_tokens_list]
        gen_wav = [Codec_model.decode_code(speech_tokens) for speech_tokens in speech_tokens]
    
    return np.concatenate([gen[0, 0, :].cpu().numpy() for gen in gen_wav])

In [0]:

display.Audio("./sample_voices/voice_preview_valentino.mp3", rate=16000)


In [0]:
long_text = """Look again at that dot. That's here. That's home. That's us. On it everyone you love, everyone you know, everyone you ever heard of, every human being who ever was, lived out their lives. The aggregate of our joy and suffering, thousands of confident religions, ideologies, and economic doctrines, every hunter and forager, every hero and coward, every creator and destroyer of civilization, every king and peasant, every young couple in love, every mother and father, hopeful child, inventor and explorer, every teacher of morals, every corrupt politician, every "superstar," every "supreme leader," every saint and sinner in the history of our species lived there--on a mote of dust suspended in a sunbeam.

The Earth is a very small stage in a vast cosmic arena. Think of the rivers of blood spilled by all those generals and emperors so that, in glory and triumph, they could become the momentary masters of a fraction of a dot. Think of the endless cruelties visited by the inhabitants of one corner of this pixel on the scarcely distinguishable inhabitants of some other corner, how frequent their misunderstandings, how eager they are to kill one another, how fervent their hatreds.

Our posturings, our imagined self-importance, the delusion that we have some privileged position in the Universe, are challenged by this point of pale light. Our planet is a lonely speck in the great enveloping cosmic dark. In our obscurity, in all this vastness, there is no hint that help will come from elsewhere to save us from ourselves.

The Earth is the only world known so far to harbor life. There is nowhere else, at least in the near future, to which our species could migrate. Visit, yes. Settle, not yet. Like it or not, for the moment the Earth is where we make our stand.

It has been said that astronomy is a humbling and character-building experience. There is perhaps no better demonstration of the folly of human conceits than this distant image of our tiny world. To me, it underscores our responsibility to deal more kindly with one another, and to preserve and cherish the pale blue dot, the only home we've ever known."""

chunk_text(long_text, min_length=250)

["Look again at that dot. That's here. That's home. That's us. On it everyone you love, everyone you know, everyone you ever heard of, every human being who ever was, lived out their lives. The aggregate of our joy and suffering,",
 'thousands of confident religions, ideologies, and economic doctrines, every hunter and forager, every hero and coward, every creator and destroyer of civilization, every king and peasant, every young couple in love, every mother and father,',
 'hopeful child, inventor and explorer, every teacher of morals, every corrupt politician, every "superstar," every "supreme leader," every saint and sinner in the history of our species lived there--on a mote of dust suspended in a sunbeam.',
 'The Earth is a very small stage in a vast cosmic arena. Think of the rivers of blood spilled by all those generals and emperors so that, in glory and triumph, they could become the momentary masters of a fraction of a dot.',
 'Think of the endless cruelties visited by the inha

In [0]:
sampling_params = SamplingParams(temperature=0.8, top_p=1, max_tokens=2048, stop=['<|SPEECH_GENERATION_END|>'], stop_token_ids=[128261])

In [0]:
audio_out = long_text_to_speech('./sample_voices/voice_preview_valentino.mp3', target_text=long_text, prompt_text="So is cheerfulness, or a good temper, the more it is spent the more remains.", chunk_length=250)
display.Audio(audio_out, rate=16000)

Processed prompts: 100%|██████████| 13/13 [00:11<00:00,  1.17it/s, est. speed input: 443.70 toks/s, output: 740.40 toks/s]


In [0]:
sf.write('./gen2.wav', audio_out, 16000)